# Serialize Attribute Profiles Classification

- [X] Read a YAML recipe
- [X] Brew recipe
- [X] Compute hashes
- [X] Write hashes
- [X] Time metrics
- [X] Result metrics
- [X] Write metrics
- [] Write/move results
- [] Watch folder
- [] Main loop
- [] Logs
- [] Catch errors
- [] Custom CVG


## Init

In [ ]:
import yaml
import numpy as np
import importlib
import sys
import hashlib
from collections import OrderedDict
import time
import os
import datetime
from sklearn import metrics
from pathlib import Path

from sklearn.ensemble import RandomForestClassifier

sys.path.append('..')
import Descriptors
from CrossValidationGenerator import APsCVG

sys.path.append('../triskele/python')
import triskele

In [ ]:
### Keep yaml ordered

def setup_yaml():
  """ https://stackoverflow.com/a/8661021 """
  represent_dict_order = lambda self, data:  self.represent_mapping('tag:yaml.org,2002:map', data.items())
  yaml.add_representer(OrderedDict, represent_dict_order)    
setup_yaml()

## Serial Classifier

In [ ]:
expe_in = '../test.yml'
expe_out = '../test_out.yml'

In [ ]:
%load_ext autoreload
%autoreload 2
with open(expe_in) as f:
    expe = OrderedDict(yaml.safe_load(f)['expe'])
display(expe)

### Compute hashes

In [ ]:
def compute_hashes(expe):
    glob = hashlib.sha1()

    expe_hashes = OrderedDict()

    for k in ['ground_truth', 'descriptors_script', 'cross_validation', 'classifier']:
        v = str(expe[k]).encode('utf-8')
        expe_hashes[k] = hashlib.sha1(v).hexdigest()
        glob.update(v)
    expe_hashes['global'] = glob.hexdigest()
    return expe_hashes

expe_hashes = compute_hashes(expe)
expe_hashes

### Write hashes

In [ ]:
with open(expe_out, 'w') as of:
    yaml.dump({'expe': expe, 'expe_hashes': expe_hashes}, of, default_flow_style=False, encoding=None, allow_unicode=True)

### Keep track of time

In [ ]:
class Kronos(object):
    def __init__(self):
        self._pt = time.process_time()
        self._times = OrderedDict()
        self._stime = time.time()
        
    def time(self, name):
        self._times[name + '_process_time'] = time.process_time() - self._pt
        self._pt = time.process_time()
        
    def get_times(self):
        return self._times
    
    def get_start_date(self):
        return self._stime
    
    def get_end_date(self):
        return time.time()
    
kronos = Kronos()

### Compute descriptors

In [ ]:
def compute_descriptors(expe):
    """Compute descriptors from a standard expe recipe"""
    script = expe['descriptors_script']
    desc = importlib.import_module(script['name'], package=Descriptors)
    #importlib.reload(Descriptors)
    att = desc.run(**script['parameters'])
    
    return att

att = compute_descriptors(expe)
kronos.time('description')

### Compute classification

In [ ]:
def compute_classification(expe, att):
    """Read a standard expe recipe and attributes, return the result classification"""
    # Ground truth
    gt = triskele.read(expe['ground_truth'])


    # CrossVal and ML
    cv = expe['cross_validation']
    cl = expe['classifier']

    prediction = np.zeros_like(gt)

    for xt, xv, yt, yv, ti in APsCVG(gt, att, **cv['parameters']):
        rfc = RandomForestClassifier(**cl['parameters'])
        rfc.fit(xt, yt)

        ypred = rfc.predict(xv)

        prediction[ti] = ypred
        
    return prediction

In [ ]:
classification = compute_classification(expe, att)
kronos.time('classification')

### Metrics

In [ ]:
def compute_metrics(ground_truth, classication):
    """Return dict of metrics for ground_truth and classification prediction in parameters"""
    f = np.nonzero(classification)
    pred = classification[f].ravel()
    gt = ground_truth[f].ravel()
    
    results = OrderedDict() 
    results['overall_accuracy'] = float(metrics.accuracy_score(gt, pred))
    results['cohen_kappa'] = float(metrics.cohen_kappa_score(gt, pred))
    
    return results

def run_metrics(expe, classification):
    """Compute the metrics from a standard expe recipe and an given classification"""
    
    ### Extensible: meta-classes
    gt = triskele.read(expe['ground_truth'])
    return compute_metrics(gt, classification)

expe_results = run_metrics(expe, classification)
expe_results

In [ ]:
kronos.time('metrics')
end_time = time.time()

### Report

In [ ]:
def create_report(kronos):
    expe_report = OrderedDict()

    expe_report['supervisor'] = os.uname()[1]

    for timev, datek in zip((kronos.get_start_date(), kronos.get_end_date()), ('start_date', 'end_date')):
        expe_report[datek] = datetime.datetime.fromtimestamp(timev).strftime('Le %d/%m/%Y à %H:%M:%S')

    ressources = kronos.get_times()
    ressources['ram'] = None

    expe_report['ressources'] = ressources
    return expe_report

expe_report = create_report(kronos)
expe_report

### Name and write prediction

In [ ]:
oname = '{}_{}'.format(Path(expe_in).stem, expe_hashes['global'][:6])
oname_tif = oname + '.tif'
oname_yml = oname + '.yml'

triskele.write(oname_tif, classification)

### Write report and results

In [ ]:
with open(oname_yml, 'w') as of:
    yaml.dump(OrderedDict({'expe': expe, 
               'expe_hashes': expe_hashes, 
               'expe_report': expe_report,
               'expe_classification': oname_tif,
               'expe_results': expe_results}), of, default_flow_style=False, encoding=None, allow_unicode=True)

In [ ]:
att.dtype

In [ ]:
import watchdog

In [ ]:
import matplotlib.pyplot as plt

plt.figure(figsize=(16, 9))
plt.imshow(prediction)
plt.show()

## Import from string module, class and instantiate

In [ ]:
import importlib
module = importlib.import_module(module_name)
class_ = getattr(module, class_name)
instance = class_()

In [ ]:
def run(rasters, treshold=1e4, areas=None, sd=None, moi=None):
    treshold = float(treshold)
    areas = None if areas is None else np.array(areas).astype(np.float).astype(np.int)
    sd = None if sd is None else np.array(sd).astype(np.float)
    moi = None if moi is None else np.array(moi).astype(np.float)
    return treshold, areas, sd, moi


In [ ]:
run(**expe['descriptors_param'])

In [ ]:
desc.

In [ ]:
sha1

In [ ]:
import hashlib

In [ ]:
hashlib.md5()

In [ ]:
sorted(expe.items())

In [ ]:
expe

In [ ]:
expe

In [ ]:
np.array(expe['descriptors_param']['areas']).astype(np.float).astype(np.int)

In [ ]:
np.array(None).astype(np.float).astype(np.int)

In [ ]:
desc = importlib.import_module(expe['descriptors_script']['path'])
desc.run(**expe['descriptors_param'])

In [ ]:
A = []

In [ ]:
A.pop()

In [ ]:
A.count()

In [ ]:
continue

In [ ]:
E = Path('./Enrichment')

In [ ]:
(E / 'Test' / 'aefaef.tif').stem

In [ ]:
E / ('qwer' + '.tif')